In [43]:
import os
import sys
from pprint import pprint
from dotenv import load_dotenv
import pandas as pd
import numpy as np
#import seaborn as sns
#import time
import xgboost as xgb
from xgboost import plot_tree
from sklearn.feature_extraction import DictVectorizer
from sklearn.pipeline import Pipeline
from sklearn.metrics import mean_squared_error
from sklearn.metrics import roc_curve
from sklearn.metrics import auc
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import RandomizedSearchCV
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import train_test_split
from sklearn.model_selection import TimeSeriesSplit
import matplotlib.pyplot as plt
import operator
import random
#conda install -c conda-forge bayesian-optimization
import BayesianOptimization
import pandas_profiling
load_dotenv('forecast_arosa.env')
random.seed(22)

# Open CSV


In [44]:
path_in = os.getenv('DATAIN') # this is where we downloaded the tabel
file_name = os.getenv('DATASET_FILENAME') # this is the file name of the dataset

In [45]:
os.path.join(path_in, file_name)

'../arosa_data/Daten_Personaleinsatzplanung_Challenge_Arosa.csv'

In [46]:
df = pd.read_csv(os.path.join(path_in, file_name))

In [47]:
df[df['Datum']=='31.08.2019']

Datum Wochentag  isFerienZH Ferien Desc ZH  isFerienSG  \
1338  31.08.2019   Samstag           0            NaN           0   

     Ferien Desc SG  isFerienGR Ferien Desc GR Feiertag Desc  isFeiertag ZH  \
1338            NaN           0            NaN           NaN              0   

      ...  is_fog_1h_idx_max  precip_1h_mm_sum  fresh_snow_1h_cm_sum  \
1338  ...                0.0              0.03                   0.0   

      wind_speed_mean_10m_1h_ms_avg  weather_symbol_1h_idx_spe  \
1338                            5.8                        2.9   

      number_of_events  Schalter  Tel  Mail  Total Anfragen  
1338                 3       183   33    23             239  

[1 rows x 36 columns]

In [48]:
df = df.iloc[1:1339]

# Overview of Data

In [49]:
df.profile_report()

# Preprocessing

In [41]:
# df['Total Anfragen'].replace('-', 0)
# df.astype({'Total Anfragen': 'int32'}).dtypes

KeyError: 'Total Anfragen'

In [50]:
df

Datum   Wochentag  isFerienZH Ferien Desc ZH  isFerienSG  \
1     02.01.2016     Samstag           0            NaN           0   
2     03.01.2016     Sonntag           0            NaN           0   
3     04.01.2016      Montag           0            NaN           0   
4     05.01.2016    Dienstag           0            NaN           0   
5     06.01.2016    Mittwoch           0            NaN           0   
...          ...         ...         ...            ...         ...   
1334  27.08.2019    Dienstag           0            NaN           0   
1335  28.08.2019    Mittwoch           0            NaN           0   
1336  29.08.2019  Donnerstag           0            NaN           0   
1337  30.08.2019     Freitag           0            NaN           0   
1338  31.08.2019     Samstag           0            NaN           0   

     Ferien Desc SG  isFerienGR Ferien Desc GR        Feiertag Desc  \
1               NaN           0            NaN        Berchtoldstag   
2               NaN           0            NaN                  NaN   
3               NaN           0            NaN                  NaN   
4               NaN           0            NaN                  NaN   
5               NaN           0            NaN  Heilige Drei Könige   
...             ...         ...            ...                  ...   
1334            NaN           0            NaN                  NaN   
1335            NaN           0            NaN                  NaN   
1336            NaN           0            NaN                  NaN   
1337            NaN           0            NaN                  NaN   
1338            NaN           0            NaN                  NaN   

      isFeiertag ZH  ...  is_fog_1h_idx_max  precip_1h_mm_sum  \
1                 0  ...                1.0              1.21   
2                 0  ...                0.0              0.23   
3                 0  ...                0.0              0.13   
4                 0  ...                0.0              0.00   
5                 0  ...                0.0              0.00   
...             ...  ...                ...               ...   
1334              0  ...                0.0              0.00   
1335              0  ...                0.0              0.00   
1336              0  ...                0.0              0.16   
1337              0  ...                0.0              0.00   
1338              0  ...                0.0              0.03   

      fresh_snow_1h_cm_sum  wind_speed_mean_10m_1h_ms_avg  \
1                      1.9                            5.4   
2                      0.0                            5.9   
3                      0.3                            2.4   
4                      0.0                            3.4   
5                      0.0                            3.0   
...                    ...                            ...   
1334                   0.0                           11.2   
1335                   0.0                            5.6   
1336                   0.0                            5.8   
1337                   0.0                            5.7   
1338                   0.0                            5.8   

      weather_symbol_1h_idx_spe  number_of_events  Schalter  Tel  Mail  \
1                           0.0                 0        78   59    22   
2                           0.0                 0         0    0     0   
3                           0.0                 0         0    0     0   
4                           1.3                 0         0    0     0   
5                           1.0                 0         0    0     0   
...                         ...               ...       ...  ...   ...   
1334                        0.0                 2        59   26    29   
1335                        1.1                 2        61   40    19   
1336                        0.0                 2        76   38    23   
1337                        0.7                 3  

# XGBoost Model

In [40]:
target_variable = 'Total Anfragen'
col_names= list(df)
X, y = df[col_names],df[target_variable]
X_train, X_test, y_train, y_test= train_test_split(X, y, test_size=0.3, random_state=123)
X_test, X_val, y_test, y_val= train_test_split(X_test, y_test, test_size=0.5, random_state=123)
nulls_per_column = X.isnull().sum()
print(nulls_per_column)

KeyError: "None of [Index(['159',   '0',   '0',   '0',   '0',  '52',  '90',  '60', '129', '129',\n       ...\n        '87',  '98',  '96',  '79', '152', '114', '120', '137', '232', '239'],\n      dtype='object', length=1338)] are in the [index]"

In [27]:
print(X[target_variable].count())
print(X_train[target_variable].count())
print(X_val[target_variable].count())
print(X_test[target_variable].count())

1338
936
201
201


In [35]:
params1 = {
    'n_jobs': 8 }

pipeline1 = Pipeline([
                     ("vectorizer", DictVectorizer(sort=False)),
                     ("clf", xgb.XGBRegressor(**params1)) 
                    ])

xgb_fit = pipeline1.fit(X_train.to_dict("records"), y_train)

TypeError: must be real number, not str

In [34]:
#Computing the MAE of our predictions
preds = xgb_fit.predict(X_test.to_dict("records"))
print("Mean Absolute Error : " + str(mean_absolute_error(preds, y_test)))

NameError: name 'mean_absolute_error' is not defined

In [33]:

accuracy = float(np.sum(preds==y_test))/y_test.shape[0] 
print("accuracy xgb_fit: %f" % (accuracy))

accuracy xgb_fit: 0.761194


In [ ]:

optimizer = BayesianOptimization(
    f=train_model,
    pbounds=bounds,
    random_state=1,
)
best = optimizer.maximize(init_points=2, n_iter= 3)
print(optimizer.max)

In [29]:
def train_model(max_depth, 
                n_estimators,
                learning_rate):
    params = {
        'n_estimators': int(n_estimators),
        'max_depth': int(max_depth),
        'learning_rate':learning_rate,
        'n_jobs': 4 #number of CPU threads
    }

    pipeline = Pipeline([
                     ("vectorizer", DictVectorizer(sort=False)),
                     ("clf", XGBRegressor(objective = 'binary:logistic',**params)),

                        ])

    xgb_fit = pipeline.fit(X_train.to_dict("records"), y_train)
    preds = xgb_fit.predict(X_val.to_dict("records"))
    accuracy = float(np.sum(preds==y_val))/y_val.shape[0] 
    return accuracy

bounds = {
    'max_depth':(5,100),
    'n_estimators': (100,10000),
    'learning_rate': (.001, 0.1),
}


In [32]:
params2 = {
    'n_estimators': int(optimizer.max['params']['n_estimators']),
    'pos_weight': pos_weight,
    'max_depth': int(optimizer.max['params']['max_depth']),
    'learning_rate':optimizer.max['params']['learning_rate'],
    'n_jobs': 4 #number of CPU threads
}

pipeline2 = Pipeline([
                     ("vectorizer", DictVectorizer(sort=False)),
                     ("clf", xgb.XGBRegressor(**params2))
                    ])

xgb_tuned_fit = pipeline2.fit(X_train.to_dict("records"), y_train)

NameError: name 'optimizer' is not defined

In [ ]:
preds_tuned = xgb_tuned_fit.predict(X_test.to_dict("records"))
preds_tuned_prob = xgb_tuned_fit.predict_proba(X_test.to_dict("records"))[:,1]
accuracy = float(np.sum(preds_tuned==y_test))/y_test.shape[0] 
print("accuracy xgb_tuned_fit: %f" % (accuracy))